# Just_the_basics_strata Neatbook
#### Get Data

In [26]:
import pandas as pd
import pandasql as ps
import numpy as np

# Get data here
df = pd.read_csv("train.csv", header=None) # Edit: Your dataset
classDF = pd.read_csv("train_labels.csv", header=None, names=["class"])
df = pd.concat([df, classDF], axis=1)
print(df.shape)
print(df.describe(include = [np.number]))
print(df.dtypes)
# print(df.describe(include = ['O']))
print(df.head())
df.dtypes



(600, 101)
                0           1            2           3           4  \
count  585.000000  590.000000   580.000000  580.000000  575.000000   
mean     0.326534    2.557716   290.594555    2.643836    0.182192   
std      0.545283    1.433982   621.384645    1.446750    0.420896   
min      0.000445    0.055685     1.007800    0.032513    0.000100   
25%      0.042475    1.350800    36.064500    1.507225    0.031295   
50%      0.079607    2.551650    93.057500    2.592850    0.060399   
75%      0.416470    3.787175   278.797500    3.951500    0.086785   
max      5.176600    5.064400  9163.100000    5.092100    4.605000   

                5           6           7           8           9     ...      \
count  584.000000  587.000000  583.000000  581.000000  581.000000     ...       
mean     2.510491    2.642292    2.552223    2.501381    0.127933     ...       
std      1.449157    1.472695    1.449577    1.451475    0.386757     ...       
min      0.014350    0.016254    0

0        float64
1        float64
2        float64
3        float64
4        float64
5        float64
6        float64
7        float64
8        float64
9        float64
10       float64
11       float64
12       float64
13       float64
14       float64
15       float64
16       float64
17       float64
18       float64
19       float64
20       float64
21       float64
22       float64
23       float64
24       float64
25       float64
26       float64
27       float64
28       float64
29       float64
          ...   
71       float64
72       float64
73       float64
74       float64
75       float64
76       float64
77       float64
78       float64
79       float64
80       float64
81       float64
82       float64
83       float64
84       float64
85       float64
86       float64
87       float64
88       float64
89       float64
90       float64
91       float64
92       float64
93       float64
94       float64
95       float64
96       float64
97       float64
98       float

#### Initialize variables

In [7]:
from sklearn.model_selection import train_test_split
className = 'class' # Edit: Replace class with the Y column name
trainX, testX, trainY, testY = train_test_split(df.drop([className], axis=1),
                                                    df[className], train_size=0.75, test_size=0.25)

indexColumns = [] # Edit: Optionally add column names
iWillManuallyCleanColumns = [] # Edit: Optionally add column names

print("trainX.shape = ", trainX.shape)
print("testX.shape = ", testX.shape)
print("trainY.shape = ", trainY.shape)
print("testY.shape = ", testY.shape)
print("\ntrainY\n")
print(trainY.head())
print("trainX\n")
print(trainX.head())



trainX.shape =  (450, 100)
testX.shape =  (150, 100)
trainY.shape =  (450,)
testY.shape =  (150,)

trainY

507    1
557    1
303    1
357    1
196    0
Name: class, dtype: int64
trainX

           0       1        2       3         4        5        6        7   \
507  0.047377  4.5405  189.030  2.3684  0.018593  0.33301  2.29570  4.33810   
557  0.356530  4.1828  144.080  5.0121  0.089036  2.16750  0.24599  2.34720   
303  1.313400  4.5131   55.012  1.3004  0.093243  1.16130  3.67080  1.36710   
357  1.132500  2.7859  425.040  4.7327  0.074033  3.16200  3.82310  0.13576   
196  0.071244  1.1237   50.006  4.9817  2.162500  3.19280  3.80820  3.94190   

         8         9     ...           90      91        92        93  \
507  3.8664  0.087997    ...     0.005185  0.3103  0.000178  0.064795   
557  1.4044  0.092030    ...     0.033801  4.2006  0.384750  0.005898   
303  3.1555  0.081447    ...     0.015155  2.3514  0.028439       NaN   
357  4.6271  0.067222    ...     0.047047  2.59

#### Clean Data

In [11]:
import numpy as np
import pandas as pd
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.model_selection import train_test_split
from sklearn.naive_bayes import GaussianNB
from sklearn.pipeline import make_pipeline, make_union
from tpot.builtins import StackingEstimator
from sklearn.metrics import accuracy_score
from sklearn.metrics import confusion_matrix
import pickle

import pandas as pd
import numpy as np
from sklearn import preprocessing
from sklearn.utils import resample
from math import ceilprin
from copy import deepcopy

class NeatData:

    def __init__(self):
        self.indexer = None # TODO: Unsure
        self.numberColumns, self.categoryColumns, self.datetimeColumns = None, None, None
        self.indexColumns, self.iWillManuallyCleanColumns = None, None
        self.columnsDropped = []
        self.finalColumnNames = None
        self.yCleaner = None

    def cleanTrainingDataset(self, trainX, trainY, indexColumns=[], iWillManuallyCleanColumns=[]):
        self.indexColumns, self.iWillManuallyCleanColumns = indexColumns, iWillManuallyCleanColumns
        trainX, trainY = self._initial(trainX, trainY)
        trainX, trainY = self._datatypeSpecific(trainX, trainY)
        trainX, trainY = self._final(trainX, trainY)
        return trainX, trainY

    def _initial(self, trainX, trainY):
        self._validateTrainingInput(trainX, trainY)
        self.yCleaner = YCleaner()
        trainX, trainY = self.yCleaner.cleanTrainingY(trainX, trainY)
        trainX, self.indexColumns, self.iWillManuallyCleanColumns = ColumnNameCleaner().execute(trainX, self.indexColumns, self.iWillManuallyCleanColumns)
        self.numberColumns, self.categoryColumns, self.datetimeColumns = ColumnDataTypeGetter().execute(trainX, self.indexColumns, self.iWillManuallyCleanColumns)
        return trainX, trainY

    def _validateTrainingInput(self, trainX, trainY):
        if len(trainY) != len(trainX.index): raise Exception('Error: trainX and trainY are differing lengths.')

    def _datatypeSpecific(self, trainX, trainY):
        self.datetimeCleaner = DatetimeCleaner()
        trainX = self.datetimeCleaner.clean(trainX, deepcopy(self.datetimeColumns))
        self.numberCleaner = NumberCleaner()
        trainX = self.numberCleaner.cleanAndLearn(trainX, deepcopy(self.numberColumns))
        self.categoryCleaner = CategoryCleaner()
        trainX = self.categoryCleaner.cleanAndLearn(trainX, self.categoryColumns, self.columnsDropped) # Rare mutates to both arrays
        return trainX, trainY

    def _final(self, trainX, trainY):
        self.indexer = Indexer() #TODO: delete this comment.  All indexing should be last in this iteration.
        trainX = self.indexer.execute(trainX, trainY, deepcopy(self.indexColumns))
        self.finalColumnNames = list(trainX)
        return trainX, trainY

    def cleanTestDataset(self, testX):
        self._validateCleanedTrainingDataset()
        return self._cleanTestDataset(testX)

    def _validateCleanedTrainingDataset(self):
        if self.finalColumnNames == None: raise Exception('Error: cleanTrainingDataset() must be run first.')

    def _cleanTestDataset(self, testX):
        ColumnNameCleaner().cleanColumnNamesOnDF(testX)
        testX = self.datetimeCleaner.clean(testX, deepcopy(self.datetimeColumns))
        testX = self.numberCleaner.clean(testX)
        testX = self.categoryCleaner.clean(testX)
        testX = self.indexer.addIndex(testX)
        testX = TestDataset().execute(testX, self.columnsDropped, self.finalColumnNames)
        return testX

    def convertYToNumbersForModeling(self, testY):
        return self.yCleaner.convertYToNumbersForModeling(testY)

    def convertYToStringsOrNumbersForPresentation(self, testY):
        return self.yCleaner.convertYToStringsOrNumbersForPresentation(testY)

class YCleaner:

    def __init__(self):
        self.yConverter = None
        self.trained = False

    def cleanTrainingY(self, trainX, trainY):
        trainY = castAsNumpy(trainY)
        trainX, trainY = MissingYRowDropper().execute(trainX, trainY)
        self._initializeYConverter(trainY)
        trainX, trainY = YBalancer().execute(trainX, trainY)
        self.trained = True
        trainY = self.convertYToNumbersForModeling(trainY)
        return trainX, trainY

    def _initializeYConverter(self, trainY):
        self.yConverter = YConverter()
        self.yConverter.setYMappings(trainY)

    def convertYToNumbersForModeling(self, trainY):
        if not self.trained: raise Exception('Error: Use cleanTrainingY(x, y) before using convertToNumber(trainY).')
        return self.yConverter.convertYToNumbersForModeling(trainY)

    def convertYToStringsOrNumbersForPresentation(self, trainY):
        if not self.trained: raise Exception('Error: Use cleanTrainingY(x, y) before using convertToString(trainY).')
        return self.yConverter.convertYToStringsOrNumbersForPresentation(trainY)

class MissingYRowDropper:

    def __init__(self):
        self.rowsToDrop = None

    def execute(self, trainX, trainY):
        self.rowsToDrop = []
        trainX['__trainY__'] = trainY
        self._appendToRowsToDropForNoneValue(trainX)
        self._appendToRowsToDropForNumbers(trainX, trainY)
        self._appendToRowsToDropForStrings(trainX, trainY)
        trainX = trainX.drop(trainX.index[self.rowsToDrop])
        trainY = trainX['__trainY__'].values
        trainX = trainX.drop(['__trainY__'], 1)
        return trainX, trainY

    def _appendToRowsToDropForNoneValue(self, trainX):
        for i, row in trainX.iterrows():
            self.rowsToDrop.append(i) if row['__trainY__'] == None else None

    def _appendToRowsToDropForNumbers(self, trainX, trainY):
        if not isStringType(trainY):
            for i, row in trainX.iterrows():
                self.rowsToDrop.append(i) if np.isnan(row['__trainY__']) else None
                self.rowsToDrop.append(i) if row['__trainY__'] == np.inf else None
                self.rowsToDrop.append(i) if row['__trainY__'] == -np.inf else None

    def _appendToRowsToDropForStrings(self, trainX, trainY):
        if isStringType(trainY):
            for i, row in trainX.iterrows():
                if row['__trainY__'] != None:
                    self.rowsToDrop.append(i) if row['__trainY__'].strip() == "" else None

class YBalancer:

    def __init__(self):
        self.trainYFrequencies, self.trainYUpsamplesNeeded = None, None
        self.trainX, self.trainY = None, None
        self.uniqueValues = None

    def execute(self, trainX, trainY):
        self.trainX, self.trainY = trainX, castAsNumpy(trainY)
        self.uniqueValues = np.unique(trainY)
        self.trainYUpsamplesNeeded = {}
        self._saveTrainYFrequencies()
        self._saveTrainYUpsamplesNeeded()
        self._fixTrainYImbalance()
        return self.trainX, self.trainY

    def _saveTrainYFrequencies(self):
        self.trainYFrequencies = pd.value_counts(self.trainY, sort=True, normalize=False)

    def _saveTrainYUpsamplesNeeded(self):
        maxCount = self._findTheMaxCount()
        minCountAllowed = ceil(maxCount / 2)
        for value in self.uniqueValues:
            actualFrequency = self.trainYFrequencies[value]
            idealTrainYFrequency = minCountAllowed if actualFrequency < minCountAllowed else actualFrequency
            self.trainYUpsamplesNeeded[value] = idealTrainYFrequency - actualFrequency

    def _findTheMaxCount(self):
        maxCount = None
        for value in self.uniqueValues:
            frequency = self.trainYFrequencies[value]
            if maxCount == None or frequency > maxCount:
                maxCount = frequency
        return maxCount

    def _fixTrainYImbalance(self):
        self.trainX['__trainY__'] = self.trainY
        for value in self.uniqueValues:
            samplesToGet = self.trainYUpsamplesNeeded[value]
            if samplesToGet > 0:
                upsampleRows = resample(self.trainX[self.trainX['__trainY__']==value],
                                    replace=True,
                                    n_samples=samplesToGet,
                                    random_state=123)
                self.trainX = pd.concat([self.trainX, upsampleRows])
        self.trainY = self.trainX['__trainY__'].values
        self.trainX = self.trainX.drop(['__trainY__'], 1)

class YConverter:

    def __init__(self):
        self._trainYMappingsStrToNum, self._trainYMappingsNumToStr = None, None
        self._trainYListOfValidInputs = None
        self._stringWasPassedToMapping = None
        self._setYMappingsWasRun = False

    def setYMappings(self, y):
        self._trainYMappingsStrToNum, self._trainYMappingsNumToStr = {'NotFound': -99}, {-99: 'NotFound'}
        self._trainYListOfValidInputs = [-99]
        self._setYMappingsWasRun = True
        self._stringWasPassedToMapping = True if isStringType(y) else False
        if not self._stringWasPassedToMapping:
            y[y == np.inf] = -99
            y[y == -np.inf] = -99
            for value in np.unique(y):
                if value != None and not np.isnan(value):
                    self._trainYListOfValidInputs.append(value)
            return
        i = 0
        for value in np.unique(y):
            if value != None and value.strip() != "":
                self._trainYMappingsStrToNum[value] = i
                self._trainYMappingsNumToStr[i] = value
                i = i + 1

    def convertYToNumbersForModeling(self, y):
        y = castAsNumpy(y)
        yIsStringType = isStringType(y)
        self._raiseExceptionsForConvertYToNumbersForModeling(yIsStringType)
        if yIsStringType and self._stringWasPassedToMapping:
            return self._convertStringToNumber(y)
        elif not yIsStringType and self._stringWasPassedToMapping:
            return self._convertNumberToNumberWithMapping(y)
        elif not yIsStringType and not self._stringWasPassedToMapping:
            return self._convertNumberToNumberWithList(y)
        else:
            raise Exception('Error: Impossible event.')

    def _raiseExceptionsForConvertYToNumbersForModeling(self, yIsStringType):
        if not self._setYMappingsWasRun: raise Exception('Error: run setYMappings before convertToNumber')
        if not self._stringWasPassedToMapping and yIsStringType: raise Exception('Error: Y was not string during setYMappings, therefore Y must be a number.')

    def _convertStringToNumber(self, y):
        y = self._prepareStringForMapping(y)
        return np.vectorize(self._trainYMappingsStrToNum.get)(y)

    def _prepareStringForMapping(self, y):
        for i in range(len(y)):
            if y[i] == None or y[i] not in self._trainYMappingsStrToNum.keys():
                y[i] = 'NotFound'
        return y

    def _convertNumberToNumberWithMapping(self, y):
        return self._prepareNumberForMapping(y)

    def _prepareNumberForMapping(self, y):
        y[y == np.inf] = -99
        y[y == -np.inf] = -99
        for i in range(len(y)):
            if np.isnan(y[i]) or y[i] not in self._trainYMappingsStrToNum.values():
                y[i] = -99
        return y

    def _convertNumberToNumberWithList(self, y):
        y[y == np.inf] = -99
        y[y == -np.inf] = -99
        for i in range(len(y)):
            if np.isnan(y[i]) or y[i] not in self._trainYListOfValidInputs:
                y[i] = -99
        return y

    def convertYToStringsOrNumbersForPresentation(self, y):
        y = castAsNumpy(y)
        yIsStringType = isStringType(y)
        self._raiseExceptionsForConvertYToStringsOrNumbersForPresentation(yIsStringType)
        if yIsStringType and self._stringWasPassedToMapping:
            return self._convertStringToString(y)
        elif not yIsStringType and self._stringWasPassedToMapping:
            return self._convertNumberToString(y)
        elif not yIsStringType and not self._stringWasPassedToMapping:
            return y
        else:
            raise Exception('Error: Impossible event.')

    def _raiseExceptionsForConvertYToStringsOrNumbersForPresentation(self, yIsStringType):
        if not self._setYMappingsWasRun: raise Exception('Error: run setYMappings before convertToString')
        if not self._stringWasPassedToMapping and yIsStringType: raise Exception('Error: Y was not string during setYMappings, so converting from string to number is not possible..')

    def _convertStringToString(self, y):
        return self._prepareStringForMapping(y)

    def _convertNumberToString(self, y):
        y = self._prepareNumberForMapping(y)
        return np.vectorize(self._trainYMappingsNumToStr.get)(y)

class ColumnNameCleaner:

    def __init__(self):
        pass

    def execute(self, trainX, indexColumns, iWillManuallyCleanColumns):
        trainX = self.cleanColumnNamesOnDF(trainX)
        indexColumns = self._cleanArrayOfColumnNames(indexColumns)
        iWillManuallyCleanColumns = self._cleanArrayOfColumnNames(iWillManuallyCleanColumns)
        return trainX, indexColumns, iWillManuallyCleanColumns

    def cleanColumnNamesOnDF(self, trainX):
        trainX.columns = trainX.columns.astype(str)
        trainX.columns = trainX.columns.str.strip().str.lower().str.replace(' ', '_')
        return trainX

    def _cleanArrayOfColumnNames(self, columns):
        if type(columns) == str:
            columns = [columns]
        arr = []
        for column in columns:
            arr.append(self._cleanColumnName(column))
        return arr

    def _cleanColumnName(self, string):
        return string.strip().lower().replace(' ', '_')

class ColumnDataTypeGetter:

    def __init__(self):
        pass

    def execute(self, trainX, indexColumns, iWillManuallyCleanColumns):
        numberColumns, categoryColumns, datetimeColumns, columns = [], [], [], trainX.columns.values.tolist()
        for column in columns:
            datatype = trainX[column].dtype
            if column in indexColumns or column in iWillManuallyCleanColumns: pass
            elif datatype == 'int64' or datatype == 'float64':
                numberColumns.append(column)
            elif datatype == 'object':
                categoryColumns.append(column)
            else:
                datetimeColumns.append(column)
                numberColumns.append(column) # Assuming dates always become numbers early when cleaning
        return numberColumns, categoryColumns, datetimeColumns

class DatetimeCleaner:

    def __init__(self):
        self.datetimeColumns = None
        self.x = None

    def clean(self, x, datetimeColumns):
        self.x, self.datetimeColumns = x, datetimeColumns
        self._convertDatetimeToNumber()
        return x

    def _convertDatetimeToNumber(self):
        for column in self.datetimeColumns:
            values = []
            for i, row in self.x.iterrows():
                values.append((pd.datetime.now() - row[column]).days)
            self.x[column] = values

class NumberCleaner:

    def __init__(self):
        self.trainX, self.numberColumns = None, None
        self.numberMetadata = None

    def cleanAndLearn(self, trainX, numberColumns):
        self.trainX, self.numberColumns = trainX, numberColumns
        self.numberMetadata = NumberMetadata()
        self.numberMetadata.train(trainX, self.numberColumns)
        return self.clean(trainX)

    def clean(self, x):
        x = NumberValueAssigner().execute(x, self.numberColumns, self.numberMetadata)
        return x

class NumberMetadata:

    def __init__(self):
        self.medians, self.lowerBounds, self.upperBounds = None, None, None

    def train(self, trainX, numberColumns):
        trainX = self._ignoreInfinityForQuantiles(trainX)

        firstQuantiles = trainX.quantile(.25)
        thirdQuantiles = trainX.quantile(.75)

        self.medians = trainX.quantile(.50)
        self.lowerBounds = {}
        self.upperBounds = {}
        for column in numberColumns:
            self.lowerBounds[column] = self.medians[column] - 2*(self.medians[column] - firstQuantiles[column])
            self.upperBounds[column] = self.medians[column] + 2*(thirdQuantiles[column] - self.medians[column])

    def _ignoreInfinityForQuantiles(self, trainX):
        return trainX.replace([np.inf, -np.inf], np.nan)

class NumberValueAssigner:

    def __init__(self):
        self.x, self.numberColumns, self.numberMetadata = None, None, None

    def execute(self, x, numberColumns, numberMetadata):
        self.x, self.numberColumns, self.numberMetadata = x, numberColumns, numberMetadata
        self._fixMissingNumValuesAndInfinity()
        self._fixHighLeveragePoints()
        return self.x

    def _fixMissingNumValuesAndInfinity(self):
        self.x = self.x.fillna(self.numberMetadata.medians) # optionally: replace self.medians with 0
        self.x = self.x.replace([-np.inf], np.nan)
        self.x = self.x.fillna(self.numberMetadata.lowerBounds)
        self.x = self.x.replace([np.inf], np.nan)
        self.x = self.x.fillna(self.numberMetadata.upperBounds)

    def _fixHighLeveragePoints(self):
        print(self.numberMetadata.upperBounds)                                   
        for i, row in self.x.iterrows():
            
            for column in self.numberColumns:
                print(column)
                print(row[column]) 
                print(row[column].dtype)                 
                if row[column] > self.numberMetadata.upperBounds[column]:
                    self.x.at[i, column] = self.numberMetadata.upperBounds[column]
                if row[column] < self.numberMetadata.lowerBounds[column]:
                    self.x.at[i, column] = self.numberMetadata.lowerBounds[column]

class CategoryCleaner:

    def __init__(self):
        self.trainX, self.categoryColumns = None, None
        self.categoryMetadata = None

    def cleanAndLearn(self, trainX, categoryColumns, columnsDropped):
        self.trainX, self.categoryColumns = trainX, categoryColumns
        self.categoryMetadata = CategoryMetadata()
        self.categoryMetadata.train(trainX, self.categoryColumns)
        self.categoryDropColumns = CategoryDropColumns()
        self.trainX = self.categoryDropColumns.execute(self.trainX, self.categoryColumns, columnsDropped)
        return self.clean(self.trainX)

    def clean(self, x):
        x = CategoryValueAssigner().execute(x, self.categoryColumns, self.categoryMetadata)
        return x

class CategoryMetadata:

    def __init__(self):
        self.trainX, self.categoryColumns = None, None
        self.valuesThatDontMapTo_Other = None
        self.categoryFrequencies = None
        self.uniqueCategoryValues = None

    def train(self, trainX, categoryColumns):
        self.trainX, self.categoryColumns = trainX, categoryColumns
        self.valuesThatDontMapTo_Other, self.categoryFrequencies = {}, {}
        self.uniqueCategoryValues = {}
        self._saveUniqueCategoryValues()
        self._saveCategoryFrequenciesAndValuesThatDontMapTo_Other()

    def _saveUniqueCategoryValues(self):
        for column in self.categoryColumns:
            self.uniqueCategoryValues[column] = []
            for value in self.trainX[column].unique():
                if value == None or pd.isnull(value):
                    continue
                else:
                    self.uniqueCategoryValues[column].append(value)
            self.uniqueCategoryValues[column].append('_Other')

    def _saveCategoryFrequenciesAndValuesThatDontMapTo_Other(self):
        for column in self.categoryColumns:
            _otherFrequency = 0
            self.valuesThatDontMapTo_Other[column] = ['_Other']
            frequencyPercentage = pd.value_counts(self.trainX[column].values, sort=False, normalize=True)
            self.categoryFrequencies[column] = {}
            for value in self.uniqueCategoryValues[column]:
                if value == '_Other':
                    continue
                elif frequencyPercentage[value] < .05:
                    _otherFrequency = _otherFrequency + frequencyPercentage[value]
                else:
                    self.valuesThatDontMapTo_Other[column].append(value)
                    self.categoryFrequencies[column][value] = frequencyPercentage[value]
            self.categoryFrequencies[column]['_Other'] = _otherFrequency

class CategoryDropColumns:

    def __init__(self):
        self.trainX, self.categoryColumns, self.columnsDropped = None, None, None

    def execute(self, trainX, categoryColumns, columnsDropped):
        self.trainX, self.categoryColumns, self.columnsDropped = trainX, categoryColumns, columnsDropped
        return self._dropCategoryColumnsWithAllMissingValues()

    def _dropCategoryColumnsWithAllMissingValues(self):
        columnsToRemove = []
        for column in self.categoryColumns:
            uniqueValues = self.trainX[column].unique()
            if len(uniqueValues) == 1 and uniqueValues[0] == None:
                columnsToRemove.append(column)
                self.columnsDropped.append(column)
                self.categoryColumns.remove(column)
        return self.trainX.drop(columnsToRemove, 1)

class CategoryValueAssigner:

    def __init__(self):
        self.x, self.categoryColumns = None, None
        self.valuesThatDontMapTo_Other = None
        self.categoryFrequencies = None
        self.uniqueCategoryValues = None

    def execute(self, x, categoryColumns, categoryMetadata):
        self.x, self.categoryColumns = x, categoryColumns
        self.valuesThatDontMapTo_Other = categoryMetadata.valuesThatDontMapTo_Other
        self.categoryFrequencies = categoryMetadata.categoryFrequencies
        self.uniqueCategoryValues = categoryMetadata.uniqueCategoryValues
        self._fixMissingCategoryValuesAndMapValuesTo_Other()
        self._applyOneHotEncoding()
        return self.x

    def _fixMissingCategoryValuesAndMapValuesTo_Other(self):
        for i, row in self.x.iterrows():
            for column in self.categoryColumns:
                if row[column] == None:
                    self.x.at[i, column] = self._getRandomCategoryBasedOnFrequencies(column)
                elif row[column] not in self.valuesThatDontMapTo_Other[column]:
                    self.x.at[i, column] = '_Other'

    def _getRandomCategoryBasedOnFrequencies(self, column):
        chosenValue, prevValue, cumulativeProbability = None, None, 0
        randomNumber = np.random.uniform(0,1,1)[0]
        for value in self.uniqueCategoryValues[column]:
            if value in self.valuesThatDontMapTo_Other[column]:
                probabilityOfValue, prevValue = self.categoryFrequencies[column][value], value
                cumulativeProbability = cumulativeProbability + probabilityOfValue
                if cumulativeProbability > randomNumber:
                    chosenValue = value
                    break
        return prevValue if chosenValue == None else chosenValue

    def _applyOneHotEncoding(self): # don't drop_first => one hot encoding instead of dummy encoding
        for column in self.categoryColumns:
            self.x = pd.concat([self.x.drop(column, axis=1), pd.get_dummies(self.x[column], prefix=column+"_", drop_first=False)], axis=1)

class Indexer:

    def __init__(self):
        self.x, self.trainY, self.indexColumns = None, None, None

    def execute(self, x, trainY, indexColumns):
        self.x, self.trainY, self.indexColumns = x, trainY, indexColumns
        self._dropDuplicatesAndMissingRowsIfIndexIsSpecified()
        x = self.addIndex(self.x)
        return x

    def _dropDuplicatesAndMissingRowsIfIndexIsSpecified(self):
        rowsToDrop = []
        if self.indexColumns != []:
            self.x['__trainY__'] = self.trainY
            self.x = self.x.drop_duplicates(subset=self.indexColumns)

            for i, row in self.x.iterrows():
                for column in self.indexColumns:
                    if ((self.x[column].dtype == 'int64' or self.x[column].dtype == 'float64') and (np.isnan(row[column]) or np.isinf(row[column]))) or row[column] == None:
                        rowsToDrop.append(i)
            self.x = self.x.drop(self.x.index[rowsToDrop])
            self.trainY = self.x['__trainY__'].values
            self.x = self.x.drop(['__trainY__'], 1)

    def addIndex(self, x):
        indexColumns = []
        x['_id'] = np.arange(1,len(x.index)+1)
        if self.indexColumns != []:
            indexColumns = list(self.indexColumns)
        indexColumns.append('_id')
        x = x.set_index(indexColumns)
        return x

class TestDataset:

    def __init__(self):
        self.x, self.columnsDropped, self.finalColumnNames = None, None, None

    def execute(self, x, columnsDropped, finalColumnNames):
        self.x, self.columnsDropped, self.finalColumnNames = x, columnsDropped, finalColumnNames
        self._newDataDropDroppedColumns()
        self._newDataAddMissingFinalColumnNames()
        self._newDataDropExtraColumnNames()
        return self.x

    def _newDataDropDroppedColumns(self):
        self.x = self.x.drop(self.columnsDropped, axis=1)

    def _newDataAddMissingFinalColumnNames(self):
        # Assuming only category columns will be missing
        for column in self.finalColumnNames:
            if column not in list(self.x):
                self.x[column] = np.zeros((len(self.x.index),1))

    def _newDataDropExtraColumnNames(self): # This hopefully does nothing - using it anyway
        columnsToDrop = []
        for column in list(self.x):
            if column not in self.finalColumnNames:
                columnsToDrop.append(column)
        self.x = self.x.drop(columnsToDrop, axis=1)

def isStringType(y):
    y = castAsNumpy(y)
    return True if y.dtype.kind in {'O', 'U', 'S'} else False

def castAsNumpy(y):
    return np.array(y)

neatdata =  NeatData()
cleanTrainX, cleanTrainY = neatdata.cleanTrainingDataset(trainX, trainY, indexColumns, iWillManuallyCleanColumns)
cleanTestX = neatdata.cleanTestDataset(testX)
cleanTestY = neatdata.convertYToNumbersForModeling(testY)

print("Cleaning done")


{'0': 0.66999599999999992, '1': 4.8937999999999997, '2': 513.05299999999988, '3': 5.3552500000000007, '4': 0.11186199999999999, '5': 4.7350500000000002, '6': 5.0898000000000003, '7': 5.1188500000000001, '8': 5.0061999999999998, '9': 0.11257700000000001, '10': 5.1645499999999993, '11': 5.0102000000000002, '12': 0.18655200000000005, '13': 5.0921000000000003, '14': 4.827, '15': 5.4220000000000006, '16': 0.133383, '17': 5.2403999999999993, '18': 4.9378000000000002, '19': 0.11504599999999998, '20': 0.10953800000000002, '21': 0.10457949999999999, '22': 5.1271000000000004, '23': 0.10778850000000001, '24': 0.11508849999999997, '25': 5.2134999999999998, '26': 4.8024000000000004, '27': 0.10325799999999999, '28': 0.39567499999999994, '29': 4.8931499999999994, '30': 0.11758800000000001, '31': 0.10672, '32': 0.12481499999999998, '33': 0.104738, '34': 5.0697999999999999, '35': 71.169000000000011, '36': 4.0363999999999987, '37': 5.2415000000000003, '38': 5.0962999999999994, '39': 1.351918, '40': 4.77

93
0.0092017
float64
94
0.043188
float64
95
0.0065665
float64
96
1.453
float64
97
4.6602
float64
98
0.0054181
float64
99
0.009481
float64
0
0.031911
float64
1
4.4118
float64
2
5.0006
float64
3
3.1336
float64
4
0.015533
float64
5
2.3879
float64
6
4.6552
float64
7
1.9705
float64
8
4.4163
float64
9
0.057071
float64
10
2.3836
float64
11
1.3454
float64
12
0.02535
float64
13
1.9797
float64
14
4.2143
float64
15
0.82842
float64
16
0.037991
float64
17
1.8291
float64
18
0.27686
float64
19
0.039833
float64
20
0.033112
float64
21
0.046397
float64
22
0.71426
float64
23
0.093071
float64
24
0.08768
float64
25
1.6989
float64
26
4.911
float64
27
0.068174
float64
28
0.045103
float64
29
3.4463
float64
30
0.00052212
float64
31
0.032554
float64
32
0.059683
float64
33
0.0787
float64
34
1.7094
float64
35
1.0568
float64
36
0.053639
float64
37
2.4151
float64
38
1.417
float64
39
0.034288
float64
40
1.0854
float64
41
2.3973
float64
42
0.046443
float64
43
2.996
float64
44
1.0343
float64
45
0.25586
float64
46
0.04

float64
5
1.8106
float64
6
2.1469
float64
7
2.2732
float64
8
2.7935
float64
9
0.083477
float64
10
3.0584
float64
11
1.5985
float64
12
0.17608
float64
13
4.3486
float64
14
2.5993
float64
15
0.4093
float64
16
0.020459
float64
17
3.2324
float64
18
3.5047
float64
19
0.054605
float64
20
0.061621
float64
21
0.071866
float64
22
4.723
float64
23
0.03987
float64
24
2.1081
float64
25
3.9988
float64
26
4.8313
float64
27
0.068361
float64
28
0.056675
float64
29
1.9753
float64
30
1.1307
float64
31
0.053796
float64
32
0.0050983
float64
33
0.015514
float64
34
4.8016
float64
35
6.0106
float64
36
3.2174
float64
37
0.56668
float64
38
3.8844
float64
39
0.051586
float64
40
1.0617
float64
41
1.5852
float64
42
0.042819
float64
43
0.38801
float64
44
2.0823
float64
45
1.8387
float64
46
0.0547
float64
47
3.2176
float64
48
0.057855
float64
49
0.044602
float64
50
2.1374
float64
51
0.068244
float64
52
0.01199
float64
53
0.037101
float64
54
2.695
float64
55
3.5543
float64
56
0.083046
float64
57
3.3631
float64
58
0.

66
3.3612
float64
67
1.4689
float64
68
0.032955
float64
69
0.02367
float64
70
4.9087
float64
71
1.2406
float64
72
0.066494
float64
73
0.003306
float64
74
2.9051
float64
75
0.0073288
float64
76
0.017977
float64
77
2.7497
float64
78
0.093555
float64
79
0.041057
float64
80
1.4113
float64
81
3.3423
float64
82
3.6755
float64
83
0.094677
float64
84
0.023004
float64
85
1.8756
float64
86
3.1834
float64
87
0.017488
float64
88
0.32732
float64
89
0.014022
float64
90
0.099657
float64
91
2.6884
float64
92
0.37648
float64
93
0.0060091
float64
94
0.089713
float64
95
0.39299
float64
96
4.3824
float64
97
3.6547
float64
98
0.046699
float64
99
0.74074
float64
0
0.076884
float64
1
0.83817
float64
2
72.09
float64
3
4.8299
float64
4
0.067504
float64
5
2.8135
float64
6
2.2126
float64
7
2.5597
float64
8
3.7146
float64
9
0.062403
float64
10
3.0232
float64
11
4.6628
float64
12
0.24386
float64
13
3.596
float64
14
4.2989
float64
15
2.215
float64
16
0.092806
float64
17
3.4745
float64
18
0.79312
float64
19
0.026405

0.00044182
float64
31
0.048517
float64
32
2.9402
float64
33
0.069039
float64
34
4.8224
float64
35
3.0298
float64
36
0.033265
float64
37
2.004
float64
38
2.708
float64
39
0.095408
float64
40
0.30983
float64
41
0.23197
float64
42
0.005105
float64
43
0.56751
float64
44
1.3168
float64
45
4.5562
float64
46
0.027651
float64
47
4.6724
float64
48
0.053201
float64
49
0.077433
float64
50
2.9109
float64
51
0.033381
float64
52
0.00076385
float64
53
0.032194
float64
54
3.6783
float64
55
1.8349
float64
56
0.046271
float64
57
0.14048
float64
58
0.027269
float64
59
2.8872
float64
60
0.074429
float64
61
0.017663
float64
62
0.06579
float64
63
0.089347
float64
64
0.0278
float64
65
4.6602
float64
66
3.9231
float64
67
3.5857
float64
68
0.037263
float64
69
0.010445
float64
70
0.68647
float64
71
4.4006
float64
72
0.055808
float64
73
0.090008
float64
74
1.674
float64
75
0.02218
float64
76
0.031749
float64
77
0.66414
float64
78
0.021909
float64
79
0.073809
float64
80
2.2839
float64
81
0.089713
float64
82
2.183

...

0.02722
float64
31
0.016843
float64
32
0.055889
float64
33
0.057059
float64
34
4.6902
float64
35
10.065
float64
36
0.020194
float64
37
4.682
float64
38
0.21653
float64
39
0.023809
float64
40
4.9642
float64
41
4.8705
float64
42
0.07936
float64
43
2.978
float64
44
5.5257
float64
45
1.0581
float64
46
0.075501
float64
47
3.7396
float64
48
0.0027876
float64
49
0.08179
float64
50
4.0186
float64
51
0.034292
float64
52
0.010793
float64
53
0.034038
float64
54
3.262
float64
55
3.0919
float64
56
0.037711
float64
57
3.8947
float64
58
0.0027691
float64
59
0.017677
float64
60
0.0069442
float64
61
0.035987
float64
62
0.033772
float64
63
0.090712
float64
64
0.097689
float64
65
4.1171
float64
66
1.2306
float64
67
2.4913
float64
68
0.025188
float64
69
0.066058
float64
70
1.1078
float64
71
2.0537
float64
72
0.05126
float64
73
0.051598
float64
74
3.4127
float64
75
0.05769
float64
76
7.1722
float64
77
0.29311
float64
78
0.090058
float64
79
0.052261
float64
80
4.3389
float64
81
0.097302
float64
82
3.8114
fl

4.4039
float64
46
0.036102
float64
47
1.4515
float64
48
0.057016
float64
49
0.52234
float64
50
4.1791
float64
51
0.034588
float64
52
0.1446
float64
53
0.22472
float64
54
3.8324
float64
55
0.49302
float64
56
0.078522
float64
57
2.8196
float64
58
0.0024288
float64
59
0.057002
float64
60
0.053397
float64
61
0.072645
float64
62
0.0077571
float64
63
0.10358
float64
64
0.11356
float64
65
2.4835
float64
66
1.4416
float64
67
2.0959
float64
68
0.066764
float64
69
0.35211
float64
70
4.2251
float64
71
0.78957
float64
72
0.14877
float64
73
0.031691
float64
74
3.3656
float64
75
0.024798
float64
76
0.085687
float64
77
4.8715
float64
78
0.065232
float64
79
0.090615
float64
80
0.17893
float64
81
0.84899
float64
82
1.5159
float64
83
0.11863
float64
84
0.0022722
float64
85
3.6987
float64
86
3.4663
float64
87
0.036341
float64
88
0.072101
float64
89
0.014674
float64
90
0.045875
float64
91
0.42862
float64
92
0.12964
float64
93
0.046099
float64
94
0.072979
float64
95
0.27165
float64
96
0.29717
float64
97
4.

4.5368
float64
30
0.058872
float64
31
0.014196
float64
32
0.077316
float64
33
0.049793
float64
34
0.32449
float64
35
4.0334
float64
36
1.784
float64
37
1.8518
float64
38
0.43621
float64
39
1.722
float64
40
0.22508
float64
41
2.5097
float64
42
0.099253
float64
43
4.8579
float64
44
1.523
float64
45
2.0569
float64
46
0.080527
float64
47
1.7063
float64
48
0.038755
float64
49
0.060624
float64
50
2.0904
float64
51
0.049483
float64
52
1.7311
float64
53
0.0015271
float64
54
5.0394
float64
55
2.6067
float64
56
0.063336
float64
57
2.1405
float64
58
0.033474
float64
59
0.077446
float64
60
0.03949
float64
61
0.095444
float64
62
0.097439
float64
63
1.7886
float64
64
0.095157
float64
65
2.2958
float64
66
1.8923
float64
67
0.72543
float64
68
0.099192
float64
69
0.0096848
float64
70
0.52454
float64
71
1.1425
float64
72
0.017892
float64
73
0.067549
float64
74
4.1158
float64
75
0.060833
float64
76
0.010788
float64
77
0.526
float64
78
0.050173
float64
79
0.6506
float64
80
2.5479
float64
81
1.7258
float64

float64
37
1.1177
float64
38
4.3779
float64
39
0.89978
float64
40
4.0341
float64
41
3.5406
float64
42
0.093186
float64
43
3.7183
float64
44
3.6869
float64
45
4.3035
float64
46
0.049214
float64
47
1.0243
float64
48
0.090282
float64
49
0.91275
float64
50
0.13935
float64
51
0.045439
float64
52
0.016927
float64
53
0.096963
float64
54
3.6269
float64
55
1.075
float64
56
0.062822
float64
57
0.55104
float64
58
0.026258
float64
59
0.01415
float64
60
0.014556
float64
61
0.059413
float64
62
0.063049
float64
63
0.072428
float64
64
0.063578
float64
65
3.1203
float64
66
2.4953
float64
67
1.1803
float64
68
0.065011
float64
69
0.47138
float64
70
1.5772
float64
71
3.1155
float64
72
0.092599
float64
73
0.0671
float64
74
2.6169
float64
75
0.056281
float64
76
0.05947
float64
77
3.6094
float64
78
0.0094542
float64
79
0.76552
float64
80
2.3423
float64
81
3.0895
float64
82
0.92076
float64
83
0.039212
float64
84
0.083168
float64
85
3.4701
float64
86
3.7318
float64
87
0.0019629
float64
88
0.066975
float64
89
0

85
0.88481
float64
86
1.0033
float64
87
0.059982
float64
88
0.061905
float64
89
0.0085879
float64
90
0.057455
float64
91
1.1489
float64
92
0.057078
float64
93
1.1343
float64
94
0.026242
float64
95
0.068694
float64
96
1.9328
float64
97
1.6447
float64
98
0.05227
float64
99
0.051212
float64
0
0.083012
float64
1
4.44
float64
2
1140.1
float64
3
5.0465
float64
4
0.069693
float64
5
4.3217
float64
6
2.6527
float64
7
4.8034
float64
8
4.9187
float64
9
0.088879
float64
10
0.60155
float64
11
2.0334
float64
12
0.062314
float64
13
0.58355
float64
14
3.4448
float64
15
1.3508
float64
16
0.040598
float64
17
3.8905
float64
18
4.5559
float64
19
0.021351
float64
20
0.0067814
float64
21
0.057862
float64
22
2.5857
float64
23
0.010093
float64
24
0.42793
float64
25
3.5943
float64
26
4.0382
float64
27
0.099356
float64
28
0.085619
float64
29
4.4481
float64
30
0.11243
float64
31
0.052768
float64
32
0.21574
float64
33
0.064961
float64
34
4.3577
float64
35
48.1
float64
36
1.2977
float64
37
2.9342
float64
38
2.7426

#### Review Cleaned Data

In [4]:
print("cleanTrainX.shape = ", trainX.shape)
print("cleanTrainY.shape = ", trainY.shape)


print(cleanTrainX.describe(include = [np.number]))
print(cleanTrainX.head())

print(cleanTrainY)


print(cleanTestX.describe(include = [np.number]))
print(cleanTestX.head())


print(cleanTestY)


cleanTrainX.shape =  (450, 101)
cleanTrainY.shape =  (450,)
                0           1           2           3           4           5  \
count  450.000000  450.000000  450.000000  450.000000  450.000000  450.000000   
mean     0.217023    2.537812  155.273834    2.669960    0.059883    2.462826   
std      0.251595    1.426742  152.458203    1.406308    0.034309    1.394823   
min      0.001702    0.114700    1.007800    0.355500    0.001462    0.023768   
25%      0.041206    1.320775   36.075000    1.521175    0.030893    1.232300   
50%      0.077118    2.482700   92.565500    2.643300    0.059066    2.538450   
75%      0.381810    3.738900  242.777500    3.914975    0.085130    3.592725   
max      0.702842    5.009500  434.584500    5.092100    0.114326    4.701050   

                6           7           8           9     ...              90  \
count  450.000000  450.000000  450.000000  450.000000     ...      450.000000   
mean     2.695786    2.558728    2.501412    0.0

#### Run TPOT

In [6]:
from tpot import TPOTClassifier

tpot = TPOTClassifier(max_time_mins=25, # Edit: Set to 480 to train for 8 hours
                      population_size=100, max_eval_time_mins=5, verbosity=2)
tpot.fit(cleanTrainX, cleanTrainY)
print(tpot.score(cleanTestX, cleanTestY))
tpot.export('tpot_pipeline.py')

print("\n\nTPOT is done.")


Version 0.9.1 of tpot is outdated. Version 0.9.2 was released Wednesday January 17, 2018.


/Users/peterjmyers/anaconda/envs/root3/lib/python3.6/site-packages/deap/creator.py:141: RuntimeWarning: A class named 'FitnessMulti' has already been created and it will be overwritten. Consider deleting previous creation of that class or rename it.
  RuntimeWarning)
/Users/peterjmyers/anaconda/envs/root3/lib/python3.6/site-packages/deap/creator.py:141: RuntimeWarning: A class named 'Individual' has already been created and it will be overwritten. Consider deleting previous creation of that class or rename it.
  RuntimeWarning)
Optimization Progress: 201pipeline [11:37,  8.92s/pipeline]                   

Generation 1 - Current best internal CV score: 0.9


Optimization Progress: 301pipeline [18:04,  1.16s/pipeline]                   

Generation 2 - Current best internal CV score: 0.9022222222222223




TPOT closed prematurely. Will use the current best pipeline.

Best pipeline: GaussianNB(GradientBoostingClassifier(input_matrix, learning_rate=0.1, max_depth=4, max_features=0.2, min_samples_leaf=5, min_samples_split=3, n_estimators=100, subsample=0.6))
0.933333333333


TPOT is done.


## Run this after TPOT is done

Creates the modelpipeline.py file.  That file also creates the trainedmodelpipeline.py.


In [ ]:
with open('modelpipeline.py', 'w') as fileOut:
    with open('tpot_pipeline.py', 'r') as fileIn:
        for line in fileIn:
            if line.startswith("import") or line.startswith("from "):
                fileOut.write(line)
    fileOut.write("""from sklearn.metrics import accuracy_score
from neatdata.neatdata import *
from sklearn.metrics import confusion_matrix
import pickle

class ModelPipeline:

    def __init__(self):
        self.indexColumns, self.iWillManuallyCleanColumns = None, None
        self.neatData =  NeatData()
        self.className = 'class' # Edit: Replace class with the Y column name
        self.indexColumns = [] # Edit: Optionally add column names
        self.iWillManuallyCleanColumns = [] # Edit: Optionally add column names
        self.cleanTrainX, self.cleanTrainY, self.cleanTestX, self.cleanTestY = None, None, None, None
        self.results = None


    def execute(self):
        trainX, testX, trainY, testY = self._getDatasetFrom________() # Edit: choose one of two functions
        self._cleanDatasets(trainX, testX, trainY, testY)
        self._modelFit()
        self._printModelScores()
        self._createTrainedModelPipelineFile()
        self._saveObjectsToDisk()
        self._createTrainedModelPipelineFile()

    def _getDatasetFromOneFile(self):
        df = pd.read_csv('iris.csv') # Edit: Your dataset
        trainX, testX, trainY, testY = train_test_split(df.drop([self.className], axis=1),
                                                         df[self.className], train_size=0.75, test_size=0.25)
        return trainX, testX, trainY, testY

    def _getDatasetFromTwoFiles(self):
        trainingDf = pd.read_csv('train_iris.csv') # Edit: Your training dataset
        testDf = pd.read_csv('test_iris.csv') # Edit: Your test dataset
        trainX = trainingDf.drop([self.className], axis=1)
        trainY = trainingDf[self.className]
        testX = testDf.drop([self.className], axis=1)
        testY = testDf[self.className]
        return trainX, testX, trainY, testY

    def _cleanDatasets(self, trainX, testX, trainY, testY):
        self.cleanTrainX, self.cleanTrainY = self.neatData.cleanTrainingDataset(trainX, trainY, self.indexColumns, self.iWillManuallyCleanColumns)
        self.cleanTestX = self.neatData.cleanTestDataset(testX)
        self.cleanTestY = self.neatData.convertYToNumbersForModeling(testY)

    def _modelFit(self):
""")

showNextLines = False
with open('modelpipeline.py', 'a') as fileOut:
    with open('tpot_pipeline.py', 'r') as fileIn:
        for line in fileIn:
            if line.startswith("# Score"):
                showNextLines = True
            elif showNextLines and not line.startswith("exported_pipeline.fit") and not line.startswith("results"):
                fileOut.write("        " + line)

with open('modelpipeline.py', 'a') as fileOut:
    fileOut.write("""        self.exported_pipeline = exported_pipeline
        self.exported_pipeline.fit(self.cleanTrainX, self.cleanTrainY)
        self.results = self.exported_pipeline.predict(self.cleanTestX)

    def _printModelScores(self):
        print("Confusion Matrix:")
        print(confusion_matrix(self.cleanTestY, self.results))
        print(accuracy_score(self.cleanTestY, self.results))

    def _saveObjectsToDisk(self):
        def save_object(obj, filename):
            with open(filename, 'wb') as output:
                pickle.dump(obj, output, pickle.HIGHEST_PROTOCOL)

        save_object(self.exported_pipeline, 'exportedPipeline.pkl')
        save_object(self.neatData, 'NeatData.pkl')

    def _createTrainedModelPipelineFile(self):
        with open('trainedmodelpipeline.py', 'w') as fileOut:
            fileOut.write(\"\"\"

import pandas as pd
import pickle

class TrainedModelPipeline:

    def __init__(self):
        self.exportedPipeline = None
        self.neatData = None
        self.testX = None
        self.cleanTestX = None
        self.results = None
        self.resultsDf = None

    def execute(self):
        self._loadObjects()
        self._getDataset()
        self._cleanDataset()
        self._predict()
        self._concatenatePredictionsToDataframe()
        self._saveResultsAsCSV()
        print("Done. Created results.csv")

    def _loadObjects(self):
        with open('exportedPipeline.pkl', 'rb') as input:
            self.exportedPipeline = pickle.load(input)
        with open('NeatData.pkl', 'rb') as input:
            self.neatData = pickle.load(input)

    def _getDataset(self):
        self.testX = pd.read_csv('test_iris.csv') # Edit: Your dataset

    def _cleanDataset(self):
        self.cleanTestX = self.neatData.cleanTestDataset(self.testX)

    def _predict(self):
        self.results = self.exportedPipeline.predict(self.cleanTestX)
        self.results = self.neatData.convertYToStringsOrNumbersForPresentation(self.results)

    def _concatenatePredictionsToDataframe(self):
        self.resultsDf = pd.DataFrame(self.results)
        self.resultsDf = pd.concat([self.testX, self.resultsDf], axis=1)

    def _saveResultsAsCSV(self):
        self.resultsDf.to_csv('./results.csv')

trainedModelPipeline = TrainedModelPipeline()
trainedModelPipeline.execute()
\"\"\")

modelPipeline = ModelPipeline()
modelPipeline.execute()


""")

print("Done creating modelpipeline.py")


In [29]:
import numpy as np
import pandas as pd
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.model_selection import train_test_split
from sklearn.naive_bayes import GaussianNB
from sklearn.pipeline import make_pipeline, make_union
from tpot.builtins import StackingEstimator
from sklearn.metrics import accuracy_score
from sklearn.metrics import confusion_matrix
import pickle

import numpy as np
import pandas as pd
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.model_selection import train_test_split
from sklearn.naive_bayes import GaussianNB
from sklearn.pipeline import make_pipeline, make_union
from tpot.builtins import StackingEstimator
from sklearn.metrics import accuracy_score
from sklearn.metrics import confusion_matrix
import pickle

import pandas as pd
import numpy as np
from sklearn import preprocessing
from sklearn.utils import resample
from math import ceil
from copy import deepcopy

class NeatData:

    def __init__(self):
        self.indexer = None # TODO: Unsure
        self.numberColumns, self.categoryColumns, self.datetimeColumns = None, None, None
        self.indexColumns, self.iWillManuallyCleanColumns = None, None
        self.columnsDropped = []
        self.finalColumnNames = None
        self.yCleaner = None

    def cleanTrainingDataset(self, trainX, trainY, indexColumns=[], iWillManuallyCleanColumns=[]):
        self.indexColumns, self.iWillManuallyCleanColumns = indexColumns, iWillManuallyCleanColumns
        trainX, trainY = self._initial(trainX, trainY)
        trainX, trainY = self._datatypeSpecific(trainX, trainY)
        trainX, trainY = self._final(trainX, trainY)
        return trainX, trainY

    def _initial(self, trainX, trainY):
        self._validateTrainingInput(trainX, trainY)
        self.yCleaner = YCleaner()
        trainX, trainY = self.yCleaner.cleanTrainingY(trainX, trainY)
        trainX, self.indexColumns, self.iWillManuallyCleanColumns = ColumnNameCleaner().execute(trainX, self.indexColumns, self.iWillManuallyCleanColumns)
        self.numberColumns, self.categoryColumns, self.datetimeColumns = ColumnDataTypeGetter().execute(trainX, self.indexColumns, self.iWillManuallyCleanColumns)
        return trainX, trainY

    def _validateTrainingInput(self, trainX, trainY):
        if len(trainY) != len(trainX.index): raise Exception('Error: trainX and trainY are differing lengths.')

    def _datatypeSpecific(self, trainX, trainY):
        self.datetimeCleaner = DatetimeCleaner()
        trainX = self.datetimeCleaner.clean(trainX, deepcopy(self.datetimeColumns))
        self.numberCleaner = NumberCleaner()
        trainX = self.numberCleaner.cleanAndLearn(trainX, deepcopy(self.numberColumns))
        self.categoryCleaner = CategoryCleaner()
        trainX = self.categoryCleaner.cleanAndLearn(trainX, self.categoryColumns, self.columnsDropped) # Rare mutates to both arrays
        return trainX, trainY

    def _final(self, trainX, trainY):
        self.indexer = Indexer() #TODO: delete this comment.  All indexing should be last in this iteration.
        trainX = self.indexer.execute(trainX, trainY, deepcopy(self.indexColumns))
        self.finalColumnNames = list(trainX)
        return trainX, trainY

    def cleanTestDataset(self, testX):
        self._validateCleanedTrainingDataset()
        return self._cleanTestDataset(testX)

    def _validateCleanedTrainingDataset(self):
        if self.finalColumnNames == None: raise Exception('Error: cleanTrainingDataset() must be run first.')

    def _cleanTestDataset(self, testX):
        ColumnNameCleaner().cleanColumnNamesOnDF(testX)
        testX = self.datetimeCleaner.clean(testX, deepcopy(self.datetimeColumns))
        testX = self.numberCleaner.clean(testX)
        testX = self.categoryCleaner.clean(testX)
        testX = self.indexer.addIndex(testX)
        testX = TestDataset().execute(testX, self.columnsDropped, self.finalColumnNames)
        return testX

    def convertYToNumbersForModeling(self, testY):
        return self.yCleaner.convertYToNumbersForModeling(testY)

    def convertYToStringsOrNumbersForPresentation(self, testY):
        return self.yCleaner.convertYToStringsOrNumbersForPresentation(testY)

class YCleaner:

    def __init__(self):
        self.yConverter = None
        self.trained = False

    def cleanTrainingY(self, trainX, trainY):
        trainY = castAsNumpy(trainY)
        trainX, trainY = MissingYRowDropper().execute(trainX, trainY)
        self._initializeYConverter(trainY)
        trainX, trainY = YBalancer().execute(trainX, trainY)
        self.trained = True
        trainY = self.convertYToNumbersForModeling(trainY)
        return trainX, trainY

    def _initializeYConverter(self, trainY):
        self.yConverter = YConverter()
        self.yConverter.setYMappings(trainY)

    def convertYToNumbersForModeling(self, trainY):
        if not self.trained: raise Exception('Error: Use cleanTrainingY(x, y) before using convertToNumber(trainY).')
        return self.yConverter.convertYToNumbersForModeling(trainY)

    def convertYToStringsOrNumbersForPresentation(self, trainY):
        if not self.trained: raise Exception('Error: Use cleanTrainingY(x, y) before using convertToString(trainY).')
        return self.yConverter.convertYToStringsOrNumbersForPresentation(trainY)

class MissingYRowDropper:

    def __init__(self):
        self.rowsToDrop = None

    def execute(self, trainX, trainY):
        self.rowsToDrop = []
        trainX['__trainY__'] = trainY
        self._appendToRowsToDropForNoneValue(trainX)
        self._appendToRowsToDropForNumbers(trainX, trainY)
        self._appendToRowsToDropForStrings(trainX, trainY)
        trainX = trainX.drop(trainX.index[self.rowsToDrop])
        trainY = trainX['__trainY__'].values
        trainX = trainX.drop(['__trainY__'], 1)
        return trainX, trainY

    def _appendToRowsToDropForNoneValue(self, trainX):
        for i, row in trainX.iterrows():
            self.rowsToDrop.append(i) if row['__trainY__'] == None else None

    def _appendToRowsToDropForNumbers(self, trainX, trainY):
        if not isStringType(trainY):
            for i, row in trainX.iterrows():
                self.rowsToDrop.append(i) if np.isnan(row['__trainY__']) else None
                self.rowsToDrop.append(i) if row['__trainY__'] == np.inf else None
                self.rowsToDrop.append(i) if row['__trainY__'] == -np.inf else None

    def _appendToRowsToDropForStrings(self, trainX, trainY):
        if isStringType(trainY):
            for i, row in trainX.iterrows():
                if row['__trainY__'] != None:
                    self.rowsToDrop.append(i) if row['__trainY__'].strip() == "" else None

class YBalancer:

    def __init__(self):
        self.trainYFrequencies, self.trainYUpsamplesNeeded = None, None
        self.trainX, self.trainY = None, None
        self.uniqueValues = None

    def execute(self, trainX, trainY):
        self.trainX, self.trainY = trainX, castAsNumpy(trainY)
        self.uniqueValues = np.unique(trainY)
        self.trainYUpsamplesNeeded = {}
        self._saveTrainYFrequencies()
        self._saveTrainYUpsamplesNeeded()
        self._fixTrainYImbalance()
        return self.trainX, self.trainY

    def _saveTrainYFrequencies(self):
        self.trainYFrequencies = pd.value_counts(self.trainY, sort=True, normalize=False)

    def _saveTrainYUpsamplesNeeded(self):
        maxCount = self._findTheMaxCount()
        minCountAllowed = ceil(maxCount / 2)
        for value in self.uniqueValues:
            actualFrequency = self.trainYFrequencies[value]
            idealTrainYFrequency = minCountAllowed if actualFrequency < minCountAllowed else actualFrequency
            self.trainYUpsamplesNeeded[value] = idealTrainYFrequency - actualFrequency

    def _findTheMaxCount(self):
        maxCount = None
        for value in self.uniqueValues:
            frequency = self.trainYFrequencies[value]
            if maxCount == None or frequency > maxCount:
                maxCount = frequency
        return maxCount

    def _fixTrainYImbalance(self):
        self.trainX['__trainY__'] = self.trainY
        for value in self.uniqueValues:
            samplesToGet = self.trainYUpsamplesNeeded[value]
            if samplesToGet > 0:
                upsampleRows = resample(self.trainX[self.trainX['__trainY__']==value],
                                    replace=True,
                                    n_samples=samplesToGet,
                                    random_state=123)
                self.trainX = pd.concat([self.trainX, upsampleRows])
        self.trainY = self.trainX['__trainY__'].values
        self.trainX = self.trainX.drop(['__trainY__'], 1)

class YConverter:

    def __init__(self):
        self._trainYMappingsStrToNum, self._trainYMappingsNumToStr = None, None
        self._trainYListOfValidInputs = None
        self._stringWasPassedToMapping = None
        self._setYMappingsWasRun = False

    def setYMappings(self, y):
        self._trainYMappingsStrToNum, self._trainYMappingsNumToStr = {'NotFound': -99}, {-99: 'NotFound'}
        self._trainYListOfValidInputs = [-99]
        self._setYMappingsWasRun = True
        self._stringWasPassedToMapping = True if isStringType(y) else False
        if not self._stringWasPassedToMapping:
            y[y == np.inf] = -99
            y[y == -np.inf] = -99
            for value in np.unique(y):
                if value != None and not np.isnan(value):
                    self._trainYListOfValidInputs.append(value)
            return
        i = 0
        for value in np.unique(y):
            if value != None and value.strip() != "":
                self._trainYMappingsStrToNum[value] = i
                self._trainYMappingsNumToStr[i] = value
                i = i + 1

    def convertYToNumbersForModeling(self, y):
        y = castAsNumpy(y)
        yIsStringType = isStringType(y)
        self._raiseExceptionsForConvertYToNumbersForModeling(yIsStringType)
        if yIsStringType and self._stringWasPassedToMapping:
            return self._convertStringToNumber(y)
        elif not yIsStringType and self._stringWasPassedToMapping:
            return self._convertNumberToNumberWithMapping(y)
        elif not yIsStringType and not self._stringWasPassedToMapping:
            return self._convertNumberToNumberWithList(y)
        else:
            raise Exception('Error: Impossible event.')

    def _raiseExceptionsForConvertYToNumbersForModeling(self, yIsStringType):
        if not self._setYMappingsWasRun: raise Exception('Error: run setYMappings before convertToNumber')
        if not self._stringWasPassedToMapping and yIsStringType: raise Exception('Error: Y was not string during setYMappings, therefore Y must be a number.')

    def _convertStringToNumber(self, y):
        y = self._prepareStringForMapping(y)
        return np.vectorize(self._trainYMappingsStrToNum.get)(y)

    def _prepareStringForMapping(self, y):
        for i in range(len(y)):
            if y[i] == None or y[i] not in self._trainYMappingsStrToNum.keys():
                y[i] = 'NotFound'
        return y

    def _convertNumberToNumberWithMapping(self, y):
        return self._prepareNumberForMapping(y)

    def _prepareNumberForMapping(self, y):
        y[y == np.inf] = -99
        y[y == -np.inf] = -99
        for i in range(len(y)):
            if np.isnan(y[i]) or y[i] not in self._trainYMappingsStrToNum.values():
                y[i] = -99
        return y

    def _convertNumberToNumberWithList(self, y):
        y[y == np.inf] = -99
        y[y == -np.inf] = -99
        for i in range(len(y)):
            if np.isnan(y[i]) or y[i] not in self._trainYListOfValidInputs:
                y[i] = -99
        return y

    def convertYToStringsOrNumbersForPresentation(self, y):
        y = castAsNumpy(y)
        yIsStringType = isStringType(y)
        self._raiseExceptionsForConvertYToStringsOrNumbersForPresentation(yIsStringType)
        if yIsStringType and self._stringWasPassedToMapping:
            return self._convertStringToString(y)
        elif not yIsStringType and self._stringWasPassedToMapping:
            return self._convertNumberToString(y)
        elif not yIsStringType and not self._stringWasPassedToMapping:
            return y
        else:
            raise Exception('Error: Impossible event.')

    def _raiseExceptionsForConvertYToStringsOrNumbersForPresentation(self, yIsStringType):
        if not self._setYMappingsWasRun: raise Exception('Error: run setYMappings before convertToString')
        if not self._stringWasPassedToMapping and yIsStringType: raise Exception('Error: Y was not string during setYMappings, so converting from string to number is not possible..')

    def _convertStringToString(self, y):
        return self._prepareStringForMapping(y)

    def _convertNumberToString(self, y):
        y = self._prepareNumberForMapping(y)
        return np.vectorize(self._trainYMappingsNumToStr.get)(y)

class ColumnNameCleaner:

    def __init__(self):
        pass

    def execute(self, trainX, indexColumns, iWillManuallyCleanColumns):
        trainX = self.cleanColumnNamesOnDF(trainX)
        indexColumns = self._cleanArrayOfColumnNames(indexColumns)
        iWillManuallyCleanColumns = self._cleanArrayOfColumnNames(iWillManuallyCleanColumns)
        return trainX, indexColumns, iWillManuallyCleanColumns

    def cleanColumnNamesOnDF(self, trainX):
        trainX.columns = trainX.columns.astype(str)
        trainX.columns = trainX.columns.str.strip().str.lower().str.replace(' ', '_')
        return trainX

    def _cleanArrayOfColumnNames(self, columns):
        if type(columns) == str:
            columns = [columns]
        arr = []
        for column in columns:
            arr.append(self._cleanColumnName(column))
        return arr

    def _cleanColumnName(self, string):
        return string.strip().lower().replace(' ', '_')

class ColumnDataTypeGetter:

    def __init__(self):
        pass

    def execute(self, trainX, indexColumns, iWillManuallyCleanColumns):
        numberColumns, categoryColumns, datetimeColumns, columns = [], [], [], trainX.columns.values.tolist()
        for column in columns:
            datatype = trainX[column].dtype
            if column in indexColumns or column in iWillManuallyCleanColumns: pass
            elif datatype == 'int64' or datatype == 'float64':
                numberColumns.append(column)
            elif datatype == 'object':
                categoryColumns.append(column)
            else:
                datetimeColumns.append(column)
                numberColumns.append(column) # Assuming dates always become numbers early when cleaning
        return numberColumns, categoryColumns, datetimeColumns

class DatetimeCleaner:

    def __init__(self):
        self.datetimeColumns = None
        self.x = None

    def clean(self, x, datetimeColumns):
        self.x, self.datetimeColumns = x, datetimeColumns
        self._convertDatetimeToNumber()
        return x

    def _convertDatetimeToNumber(self):
        for column in self.datetimeColumns:
            values = []
            for i, row in self.x.iterrows():
                values.append((pd.datetime.now() - row[column]).days)
            self.x[column] = values

class NumberCleaner:

    def __init__(self):
        self.trainX, self.numberColumns = None, None
        self.numberMetadata = None

    def cleanAndLearn(self, trainX, numberColumns):
        self.trainX, self.numberColumns = trainX, numberColumns
        self.numberMetadata = NumberMetadata()
        self.numberMetadata.train(trainX, self.numberColumns)
        return self.clean(trainX)

    def clean(self, x):
        x = NumberValueAssigner().execute(x, self.numberColumns, self.numberMetadata)
        return x

class NumberMetadata:

    def __init__(self):
        self.medians, self.lowerBounds, self.upperBounds = None, None, None

    def train(self, trainX, numberColumns):
        trainX = self._ignoreInfinityForQuantiles(trainX)

        firstQuantiles = trainX.quantile(.25)
        thirdQuantiles = trainX.quantile(.75)

        self.medians = trainX.quantile(.50)
        self.lowerBounds = {}
        self.upperBounds = {}
        for column in numberColumns:
            self.lowerBounds[column] = self.medians[column] - 2*(self.medians[column] - firstQuantiles[column])
            self.upperBounds[column] = self.medians[column] + 2*(thirdQuantiles[column] - self.medians[column])

    def _ignoreInfinityForQuantiles(self, trainX):
        return trainX.replace([np.inf, -np.inf], np.nan)

class NumberValueAssigner:

    def __init__(self):
        self.x, self.numberColumns, self.numberMetadata = None, None, None

    def execute(self, x, numberColumns, numberMetadata):
        self.x, self.numberColumns, self.numberMetadata = x, numberColumns, numberMetadata
        self._fixMissingNumValuesAndInfinity()
        self._fixHighLeveragePoints()
        return self.x

    def _fixMissingNumValuesAndInfinity(self):
        self.x = self.x.fillna(self.numberMetadata.medians) # optionally: replace self.medians with 0
        self.x = self.x.replace([-np.inf], np.nan)
        self.x = self.x.fillna(self.numberMetadata.lowerBounds)
        self.x = self.x.replace([np.inf], np.nan)
        self.x = self.x.fillna(self.numberMetadata.upperBounds)

    def _fixHighLeveragePoints(self):
        print(self.numberMetadata.upperBounds)                                   
        for i, row in self.x.iterrows():
        
            for column in self.numberColumns:               
                if row[column] > self.numberMetadata.upperBounds[column]:
                    self.x.at[i, column] = self.numberMetadata.upperBounds[column]
                if row[column] < self.numberMetadata.lowerBounds[column]:
                    self.x.at[i, column] = self.numberMetadata.lowerBounds[column]

class CategoryCleaner:

    def __init__(self):
        self.trainX, self.categoryColumns = None, None
        self.categoryMetadata = None

    def cleanAndLearn(self, trainX, categoryColumns, columnsDropped):
        self.trainX, self.categoryColumns = trainX, categoryColumns
        self.categoryMetadata = CategoryMetadata()
        self.categoryMetadata.train(trainX, self.categoryColumns)
        self.categoryDropColumns = CategoryDropColumns()
        self.trainX = self.categoryDropColumns.execute(self.trainX, self.categoryColumns, columnsDropped)
        return self.clean(self.trainX)

    def clean(self, x):
        x = CategoryValueAssigner().execute(x, self.categoryColumns, self.categoryMetadata)
        return x

class CategoryMetadata:

    def __init__(self):
        self.trainX, self.categoryColumns = None, None
        self.valuesThatDontMapTo_Other = None
        self.categoryFrequencies = None
        self.uniqueCategoryValues = None

    def train(self, trainX, categoryColumns):
        self.trainX, self.categoryColumns = trainX, categoryColumns
        self.valuesThatDontMapTo_Other, self.categoryFrequencies = {}, {}
        self.uniqueCategoryValues = {}
        self._saveUniqueCategoryValues()
        self._saveCategoryFrequenciesAndValuesThatDontMapTo_Other()

    def _saveUniqueCategoryValues(self):
        for column in self.categoryColumns:
            self.uniqueCategoryValues[column] = []
            for value in self.trainX[column].unique():
                if value == None or pd.isnull(value):
                    continue
                else:
                    self.uniqueCategoryValues[column].append(value)
            self.uniqueCategoryValues[column].append('_Other')

    def _saveCategoryFrequenciesAndValuesThatDontMapTo_Other(self):
        for column in self.categoryColumns:
            _otherFrequency = 0
            self.valuesThatDontMapTo_Other[column] = ['_Other']
            frequencyPercentage = pd.value_counts(self.trainX[column].values, sort=False, normalize=True)
            self.categoryFrequencies[column] = {}
            for value in self.uniqueCategoryValues[column]:
                if value == '_Other':
                    continue
                elif frequencyPercentage[value] < .05:
                    _otherFrequency = _otherFrequency + frequencyPercentage[value]
                else:
                    self.valuesThatDontMapTo_Other[column].append(value)
                    self.categoryFrequencies[column][value] = frequencyPercentage[value]
            self.categoryFrequencies[column]['_Other'] = _otherFrequency

class CategoryDropColumns:

    def __init__(self):
        self.trainX, self.categoryColumns, self.columnsDropped = None, None, None

    def execute(self, trainX, categoryColumns, columnsDropped):
        self.trainX, self.categoryColumns, self.columnsDropped = trainX, categoryColumns, columnsDropped
        return self._dropCategoryColumnsWithAllMissingValues()

    def _dropCategoryColumnsWithAllMissingValues(self):
        columnsToRemove = []
        for column in self.categoryColumns:
            uniqueValues = self.trainX[column].unique()
            if len(uniqueValues) == 1 and uniqueValues[0] == None:
                columnsToRemove.append(column)
                self.columnsDropped.append(column)
                self.categoryColumns.remove(column)
        return self.trainX.drop(columnsToRemove, 1)

class CategoryValueAssigner:

    def __init__(self):
        self.x, self.categoryColumns = None, None
        self.valuesThatDontMapTo_Other = None
        self.categoryFrequencies = None
        self.uniqueCategoryValues = None

    def execute(self, x, categoryColumns, categoryMetadata):
        self.x, self.categoryColumns = x, categoryColumns
        self.valuesThatDontMapTo_Other = categoryMetadata.valuesThatDontMapTo_Other
        self.categoryFrequencies = categoryMetadata.categoryFrequencies
        self.uniqueCategoryValues = categoryMetadata.uniqueCategoryValues
        self._fixMissingCategoryValuesAndMapValuesTo_Other()
        self._applyOneHotEncoding()
        return self.x

    def _fixMissingCategoryValuesAndMapValuesTo_Other(self):
        for i, row in self.x.iterrows():
            for column in self.categoryColumns:
                if row[column] == None:
                    self.x.at[i, column] = self._getRandomCategoryBasedOnFrequencies(column)
                elif row[column] not in self.valuesThatDontMapTo_Other[column]:
                    self.x.at[i, column] = '_Other'

    def _getRandomCategoryBasedOnFrequencies(self, column):
        chosenValue, prevValue, cumulativeProbability = None, None, 0
        randomNumber = np.random.uniform(0,1,1)[0]
        for value in self.uniqueCategoryValues[column]:
            if value in self.valuesThatDontMapTo_Other[column]:
                probabilityOfValue, prevValue = self.categoryFrequencies[column][value], value
                cumulativeProbability = cumulativeProbability + probabilityOfValue
                if cumulativeProbability > randomNumber:
                    chosenValue = value
                    break
        return prevValue if chosenValue == None else chosenValue

    def _applyOneHotEncoding(self): # don't drop_first => one hot encoding instead of dummy encoding
        for column in self.categoryColumns:
            self.x = pd.concat([self.x.drop(column, axis=1), pd.get_dummies(self.x[column], prefix=column+"_", drop_first=False)], axis=1)

class Indexer:

    def __init__(self):
        self.x, self.trainY, self.indexColumns = None, None, None

    def execute(self, x, trainY, indexColumns):
        self.x, self.trainY, self.indexColumns = x, trainY, indexColumns
        self._dropDuplicatesAndMissingRowsIfIndexIsSpecified()
        x = self.addIndex(self.x)
        return x

    def _dropDuplicatesAndMissingRowsIfIndexIsSpecified(self):
        rowsToDrop = []
        if self.indexColumns != []:
            self.x['__trainY__'] = self.trainY
            self.x = self.x.drop_duplicates(subset=self.indexColumns)

            for i, row in self.x.iterrows():
                for column in self.indexColumns:
                    if ((self.x[column].dtype == 'int64' or self.x[column].dtype == 'float64') and (np.isnan(row[column]) or np.isinf(row[column]))) or row[column] == None:
                        rowsToDrop.append(i)
            self.x = self.x.drop(self.x.index[rowsToDrop])
            self.trainY = self.x['__trainY__'].values
            self.x = self.x.drop(['__trainY__'], 1)

    def addIndex(self, x):
        indexColumns = []
        x['_id'] = np.arange(1,len(x.index)+1)
        if self.indexColumns != []:
            indexColumns = list(self.indexColumns)
        indexColumns.append('_id')
        x = x.set_index(indexColumns)
        return x

class TestDataset:

    def __init__(self):
        self.x, self.columnsDropped, self.finalColumnNames = None, None, None

    def execute(self, x, columnsDropped, finalColumnNames):
        self.x, self.columnsDropped, self.finalColumnNames = x, columnsDropped, finalColumnNames
        self._newDataDropDroppedColumns()
        self._newDataAddMissingFinalColumnNames()
        self._newDataDropExtraColumnNames()
        return self.x

    def _newDataDropDroppedColumns(self):
        self.x = self.x.drop(self.columnsDropped, axis=1)

    def _newDataAddMissingFinalColumnNames(self):
        # Assuming only category columns will be missing
        for column in self.finalColumnNames:
            if column not in list(self.x):
                self.x[column] = np.zeros((len(self.x.index),1))

    def _newDataDropExtraColumnNames(self): # This hopefully does nothing - using it anyway
        columnsToDrop = []
        for column in list(self.x):
            if column not in self.finalColumnNames:
                columnsToDrop.append(column)
        self.x = self.x.drop(columnsToDrop, axis=1)

def isStringType(y):
    y = castAsNumpy(y)
    return True if y.dtype.kind in {'O', 'U', 'S'} else False

def castAsNumpy(y):
    return np.array(y)

class ModelPipeline:

    def __init__(self):
        self.indexColumns, self.iWillManuallyCleanColumns = None, None
        self.neatData =  NeatData()
        self.className = 'class' # Edit: Replace class with the Y column name
        self.indexColumns = [] # Edit: Optionally add column names
        self.iWillManuallyCleanColumns = [] # Edit: Optionally add column names
        self.cleanTrainX, self.cleanTrainY, self.cleanTestX, self.cleanTestY = None, None, None, None
        self.results = None


    def execute(self):
        trainX, testX, trainY, testY = self._getDatasetFromOneFile() # Edit: choose one of two functions
        self._cleanDatasets(trainX, testX, trainY, testY)
        self._modelFit()
        self._printModelScores()
        self._createTrainedModelPipelineFile()
        self._saveObjectsToDisk()
        self._createTrainedModelPipelineFile()

    def _getDatasetFromOneFile(self):
        df = pd.read_csv("train.csv", header=None) # Edit: Your dataset
        classDF = pd.read_csv("train_labels.csv", header=None, names=["class"])
        df = pd.concat([df, classDF], axis=1)

        trainX, testX, trainY, testY = train_test_split(df.drop([self.className], axis=1),
                                                         df[self.className], train_size=0.75, test_size=0.25)
        return trainX, testX, trainY, testY

    def _getDatasetFromTwoFiles(self):
        trainingDf = pd.read_csv('train_iris.csv') # Edit: Your training dataset
        testDf = pd.read_csv('test_iris.csv') # Edit: Your test dataset
        trainX = trainingDf.drop([self.className], axis=1)
        trainY = trainingDf[self.className]
        testX = testDf.drop([self.className], axis=1)
        testY = testDf[self.className]
        return trainX, testX, trainY, testY

    def _cleanDatasets(self, trainX, testX, trainY, testY):
        self.cleanTrainX, self.cleanTrainY = self.neatData.cleanTrainingDataset(trainX, trainY, self.indexColumns, self.iWillManuallyCleanColumns)
        self.cleanTestX = self.neatData.cleanTestDataset(testX)
        self.cleanTestY = self.neatData.convertYToNumbersForModeling(testY)

    def _modelFit(self):
        exported_pipeline = make_pipeline(
            StackingEstimator(estimator=GradientBoostingClassifier(learning_rate=0.1, max_depth=4, max_features=0.2, min_samples_leaf=5, min_samples_split=3, n_estimators=100, subsample=0.6000000000000001)),
            GaussianNB()
        )

        self.exported_pipeline = exported_pipeline
        self.exported_pipeline.fit(self.cleanTrainX, self.cleanTrainY)
        self.results = self.exported_pipeline.predict(self.cleanTestX)

    def _printModelScores(self):
        print("Confusion Matrix:")
        print(confusion_matrix(self.cleanTestY, self.results))
        print(accuracy_score(self.cleanTestY, self.results))

    def _saveObjectsToDisk(self):
        def save_object(obj, filename):
            with open(filename, 'wb') as output:
                pickle.dump(obj, output, pickle.HIGHEST_PROTOCOL)

        save_object(self.exported_pipeline, 'exportedPipeline.pkl')
        save_object(self.neatData, 'NeatData.pkl')

    def _createTrainedModelPipelineFile(self):
        with open('trainedmodelpipeline.py', 'w') as fileOut:
            fileOut.write("""

import pandas as pd
import pickle

class TrainedModelPipeline:

    def __init__(self):
        self.exportedPipeline = None
        self.neatData = None
        self.testX = None
        self.cleanTestX = None
        self.results = None
        self.resultsDf = None

    def execute(self):
        self._loadObjects()
        self._getDataset()
        self._cleanDataset()
        self._predict()
        self._concatenatePredictionsToDataframe()
        self._saveResultsAsCSV()
        print("Done. Created results.csv")

    def _loadObjects(self):
        with open('exportedPipeline.pkl', 'rb') as input:
            self.exportedPipeline = pickle.load(input)
        with open('NeatData.pkl', 'rb') as input:
            self.neatData = pickle.load(input)

    def _getDataset(self):
        self.testX = pd.read_csv('test_iris.csv') # Edit: Your dataset

    def _cleanDataset(self):
        self.cleanTestX = self.neatData.cleanTestDataset(self.testX)

    def _predict(self):
        self.results = self.exportedPipeline.predict(self.cleanTestX)
        self.results = self.neatData.convertYToStringsOrNumbersForPresentation(self.results)

    def _concatenatePredictionsToDataframe(self):
        self.resultsDf = pd.DataFrame(self.results)
        self.resultsDf = pd.concat([self.testX, self.resultsDf], axis=1)

    def _saveResultsAsCSV(self):
        self.resultsDf.to_csv('./results.csv')

trainedModelPipeline = TrainedModelPipeline()
trainedModelPipeline.execute()
""")

modelPipeline = ModelPipeline()
modelPipeline.execute()


{'0': 0.79240899999999992, '1': 4.9419000000000004, '2': 428.11799999999994, '3': 5.4108500000000008, '4': 0.11419000000000001, '5': 4.9748999999999999, '6': 5.1073000000000004, '7': 5.1969000000000003, '8': 4.9837999999999996, '9': 0.11462550000000001, '10': 5.2766999999999999, '11': 5.0358000000000001, '12': 0.161495, '13': 4.9607000000000001, '14': 5.2952500000000011, '15': 5.2103999999999999, '16': 0.13415700000000003, '17': 4.9590000000000005, '18': 4.9215, '19': 0.11368400000000001, '20': 0.10956000000000002, '21': 0.102053, '22': 5.1675000000000004, '23': 0.108541, '24': 0.11350099999999999, '25': 5.21875, '26': 4.7723500000000003, '27': 0.102885, '28': 0.38752500000000012, '29': 4.7241499999999998, '30': 0.123002, '31': 0.10738300000000001, '32': 0.12448300000000001, '33': 0.10651649999999999, '34': 5.0696500000000002, '35': 76.52600000000001, '36': 3.6796999999999995, '37': 5.1749999999999998, '38': 4.9829999999999997, '39': 1.428245, '40': 4.8009499999999994, '41': 5.09594999

float64
84
0.01608
float64
85
0.21059
float64
86
2.7711
float64
87
0.08475
float64
88
0.041229
float64
89
0.42403
float64
90
0.032139
float64
91
4.0415
float64
92
0.027387
float64
93
0.097016
float64
94
0.025267
float64
95
0.48414
float64
96
3.6421
float64
97
2.6042
float64
98
0.056142
float64
99
0.070112
float64
0
0.048092
float64
1
3.9229
float64
2
36.054
float64
3
1.7254
float64
4
0.031795
float64
5
0.51962
float64
6
0.65735
float64
7
2.2758
float64
8
4.4545
float64
9
0.083824
float64
10
2.6639
float64
11
3.6878
float64
12
0.093464
float64
13
1.6196
float64
14
2.7676
float64
15
4.5777
float64
16
0.032184
float64
17
3.293
float64
18
0.78974
float64
19
0.023442
float64
20
0.070901
float64
21
0.093728
float64
22
3.7137
float64
23
0.0175
float64
24
0.062022
float64
25
2.9007
float64
26
2.3633
float64
27
0.046009
float64
28
0.40103
float64
29
3.5453
float64
30
0.0028712
float64
31
0.01986
float64
32
0.032184
float64
33
0.045653
float64
34
4.3038
float64
35
11.022
float64
36
0.092004
floa

float64
15
2.4755
float64
16
0.079339
float64
17
0.83866
float64
18
2.9218
float64
19
0.084288
float64
20
0.05964
float64
21
0.052491
float64
22
2.8415
float64
23
0.099371
float64
24
0.60748
float64
25
0.31336
float64
26
3.7825
float64
27
0.00051587
float64
28
0.17926
float64
29
2.9255
float64
30
0.77094
float64
31
0.066671
float64
32
0.086006
float64
33
0.050669
float64
34
2.7716
float64
35
696.06
float64
36
1.4374
float64
37
2.4372
float64
38
0.18602
float64
39
0.7042
float64
40
2.3165
float64
41
0.77391
float64
42
0.05771
float64
43
1.9691
float64
44
8.5355
float64
45
4.296
float64
46
0.09555
float64
47
4.7459
float64
48
0.010036
float64
49
1.2565
float64
50
0.35085
float64
51
0.0020805
float64
52
0.16253
float64
53
0.19464
float64
54
0.85575
float64
55
4.5898
float64
56
0.071956
float64
57
2.3511
float64
58
0.10208
float64
59
0.038206
float64
60
0.36207
float64
61
0.06312
float64
62
0.041536
float64
63
0.82134
float64
64
1.4802
float64
65
3.8685
float64
66
1.5422
float64
67
4.5485


float64
37
4.2847
float64
38
2.491
float64
39
0.04829
float64
40
0.19385
float64
41
0.43992
float64
42
0.25473
float64
43
0.35222
float64
44
3.4913
float64
45
2.6502
float64
46
0.033129
float64
47
1.366
float64
48
0.30001
float64
49
0.057904
float64
50
3.5016
float64
51
0.037028
float64
52
0.29098
float64
53
0.26467
float64
54
1.2159
float64
55
2.56075
float64
56
3.6383
float64
57
2.6238
float64
58
0.030916
float64
59
0.079491
float64
60
0.053448
float64
61
0.033338
float64
62
0.28562
float64
63
0.7245
float64
64
0.099822
float64
65
2.1236
float64
66
1.3775
float64
67
1.6942
float64
68
0.30309
float64
69
0.31843
float64
70
1.6376
float64
71
1.2801
float64
72
0.53488
float64
73
0.016991
float64
74
3.8967
float64
75
0.25175
float64
76
0.08776
float64
77
1.4595
float64
78
0.26904
float64
79
0.4686
float64
80
1.6719
float64
81
0.49343
float64
82
1.6949
float64
83
0.09771
float64
84
0.68526
float64
85
2.1632
float64
86
3.3903
float64
87
0.90131
float64
88
1.4239
float64
89
0.0058546
float64

float64
11
4.6651
float64
12
0.077048
float64
13
0.56457
float64
14
0.41168
float64
15
3.7656
float64
16
0.076525
float64
17
3.4546
float64
18
4.3566
float64
19
0.061511
float64
20
0.084637
float64
21
0.048996
float64
22
4.7424
float64
23
0.061783
float64
24
0.092881
float64
25
1.6054
float64
26
1.8432
float64
27
0.035539
float64
28
0.0041667
float64
29
0.092234
float64
30
0.056058
float64
31
2.488e-05
float64
32
0.00055349
float64
33
0.085211
float64
34
5.015
float64
35
1.0423
float64
36
0.044853
float64
37
1.7584
float64
38
3.2945
float64
39
0.045645
float64
40
3.3026
float64
41
1.6954
float64
42
0.038968
float64
43
3.5916
float64
44
1.0214
float64
45
1.2582
float64
46
0.042295
float64
47
3.5645
float64
48
0.0976
float64
49
0.0086173
float64
50
3.5061
float64
51
0.089135
float64
52
0.0060223
float64
53
0.010378
float64
54
2.0653
float64
55
2.9764
float64
56
0.092323
float64
57
0.97037
float64
58
0.084375
float64
59
0.013377
float64
60
0.054292
float64
61
0.047457
float64
62
0.032017


...

40
2.0567
float64
41
4.5981
float64
42
0.011959
float64
43
1.2374
float64
44
1.3456
float64
45
4.0075
float64
46
0.010623
float64
47
2.7919
float64
48
0.29306
float64
49
0.29176
float64
50
3.195
float64
51
0.00039256
float64
52
0.054088
float64
53
0.072414
float64
54
3.9032
float64
55
2.0568
float64
56
0.28988
float64
57
0.74675
float64
58
0.097103
float64
59
0.097509
float64
60
0.075185
float64
61
0.34338
float64
62
0.054406
float64
63
0.28385
float64
64
0.039725
float64
65
4.9853
float64
66
2.5413
float64
67
0.11368
float64
68
0.032167
float64
69
0.099161
float64
70
3.5879
float64
71
2.5695
float64
72
0.020604
float64
73
0.050407
float64
74
4.234
float64
75
0.024661
float64
76
0.28586
float64
77
3.4982
float64
78
0.063162
float64
79
0.024661
float64
80
1.1881
float64
81
0.2644
float64
82
2.8276
float64
83
0.34735
float64
84
0.084691
float64
85
0.5641
float64
86
1.6588
float64
87
0.02469
float64
88
0.014195
float64
89
0.055393
float64
90
0.00084503
float64
91
2.0191
float64
92
0.04848

float64
10
0.94364
float64
11
3.2929
float64
12
0.2271
float64
13
0.70515
float64
14
2.2874
float64
15
2.6434
float64
16
0.066203
float64
17
2.6717
float64
18
0.85795
float64
19
0.033282
float64
20
0.073681
float64
21
0.087791
float64
22
3.8062
float64
23
0.012308
float64
24
0.052709
float64
25
1.6739
float64
26
1.768
float64
27
0.060114
float64
28
0.41862
float64
29
2.9596
float64
30
0.0060652
float64
31
0.020148
float64
32
1.0613
float64
33
0.032065
float64
34
1.2414
float64
35
28.06
float64
36
3.1659
float64
37
3.7725
float64
38
1.6692
float64
39
0.05476
float64
40
2.74035
float64
41
1.9395
float64
42
0.059041
float64
43
5.0365
float64
44
3.3769
float64
45
1.5504
float64
46
0.055102
float64
47
4.3801
float64
48
0.095994
float64
49
0.036033
float64
50
4.3266
float64
51
0.089639
float64
52
1.145
float64
53
0.076482
float64
54
4.8146
float64
55
4.2532
float64
56
0.025349
float64
57
2.5806
float64
58
0.096362
float64
59
0.011201
float64
60
0.025341
float64
61
0.0081277
float64
62
0.0732

4.409
float64
30
0.030356
float64
31
0.05348
float64
32
0.078518
float64
33
0.046797
float64
34
2.1551
float64
35
28.009
float64
36
0.91619
float64
37
0.32053
float64
38
1.5473
float64
39
0.075279
float64
40
3.1394
float64
41
0.66658
float64
42
0.039449
float64
43
1.3998
float64
44
2.44835
float64
45
0.38808
float64
46
0.021814
float64
47
4.2637
float64
48
0.021844
float64
49
0.034375
float64
50
1.8603
float64
51
0.074929
float64
52
0.0043284
float64
53
0.070437
float64
54
4.7937
float64
55
2.1308
float64
56
0.041288
float64
57
2.3475
float64
58
0.076057
float64
59
0.083137
float64
60
0.071933
float64
61
0.050938
float64
62
0.014873
float64
63
0.025144
float64
64
0.07689
float64
65
2.9522
float64
66
3.9852
float64
67
1.2165
float64
68
0.053042
float64
69
0.0026807
float64
70
0.27011
float64
71
4.9544
float64
72
0.98886
float64
73
0.060877
float64
74
1.7128
float64
75
0.068643
float64
76
0.032332
float64
77
3.5314
float64
78
0.0089202
float64
79
0.57132
float64
80
0.27333
float64
81
3.6

1.656
float64
92
0.088253
float64
93
0.052877
float64
94
0.069516
float64
95
0.034791
float64
96
2.0423
float64
97
4.4688
float64
98
0.06348
float64
99
0.05497
float64
0
0.091349
float64
1
3.1599
float64
2
94.042
float64
3
1.5689
float64
4
0.063457
float64
5
4.7381
float64
6
3.8314
float64
7
0.31442
float64
8
1.9236
float64
9
0.088997
float64
10
1.371
float64
11
2.3803
float64
12
0.040811
float64
13
1.5487
float64
14
2.5711
float64
15
1.0319
float64
16
0.026309
float64
17
4.6012
float64
18
2.1583
float64
19
0.054892
float64
20
0.079739
float64
21
0.064454
float64
22
4.1545
float64
23
0.020147
float64
24
0.061489
float64
25
0.079811
float64
26
3.5573
float64
27
0.015942
float64
28
0.28053
float64
29
1.2205
float64
30
0.042382
float64
31
0.073758
float64
32
0.015476
float64
33
0.097062
float64
34
2.7317
float64
35
1.0344
float64
36
1.7105
float64
37
3.6477
float64
38
0.085277
float64
39
1.1728
float64
40
3.2214
float64
41
3.5716
float64
42
0.051736
float64
43
3.3823
float64
44
1.0084
flo

75
0.052608
float64
76
0.052248
float64
77
1.8823
float64
78
0.097153
float64
79
0.028803
float64
80
2.5141
float64
81
0.029656
float64
82
0.8511
float64
83
0.069457
float64
84
0.051028
float64
85
3.1673
float64
86
5.0407
float64
87
0.073052
float64
88
0.023888
float64
89
0.045688
float64
90
0.035396
float64
91
0.57432
float64
92
0.014665
float64
93
0.058106
float64
94
0.0824
float64
95
0.043336
float64
96
2.1565
float64
97
4.5839
float64
98
0.025464
float64
99
0.016601
float64
0
0.29173
float64
1
3.7062
float64
2
491.09
float64
3
3.019
float64
4
0.027645
float64
5
3.0042
float64
6
4.7058
float64
7
2.0857
float64
8
1.2193
float64
9
0.065123
float64
10
2.7787
float64
11
3.2857
float64
12
0.11696
float64
13
0.69042
float64
14
4.4404
float64
15
1.0317
float64
16
0.66552
float64
17
0.58705
float64
18
3.2369
float64
19
0.084797
float64
20
0.075465
float64
21
0.063818
float64
22
2.8176
float64
23
0.046247
float64
24
0.030598
float64
25
2.8458
float64
26
1.3784
float64
27
0.037065
float64
28
